# Zusammenfassung der Analysen vom Hackathon für die Webside

- womöglich zur Darstellung auf der Webside


In [1]:
import numpy as np
import pandas as pd
import altair as alt

## Daten aufbereitung

Dump der Datenbank vom 25.03.2023. Die verschiedene Tabellen der Datenbank werden einzeln eingelesen. Zusätzlich werden alle direkt zu einem Tweet zugehörige Information in ein Datenobjekt gesammelt. Die Informationen zu den GIS-Daten zu den einzelnen Polizeistadtion ("police_stations") sind noch unvollständig und müssen gegebenfalls nocheinmal überprüft werden.



In [45]:
# Merging different table of old (~2021) and new (~2022) scraper

## cols: hashtag, url, mention (same for both)
tweets_meta = pd.concat([pd.read_csv("data/entity_old.tsv", sep = "\t"), # data from old scraper
                         pd.read_csv("data/tweets.csv")]) # data from new scraper

## cols: id, tweet_text, created_at, user_id; only subset from old table (same tsv used in next step)
tweets_text = pd.concat([pd.read_csv("data/tweet_old.tsv", sep = "\t")[['id','tweet_text', 'created_at', 'user_id']].rename(columns = {"id":"tweet_id"}),
                         pd.read_csv("data/tweets-1679742698645.csv")])

## cols: id, like_count, retweet_count, reply_count, quote_count; only subset from old table
tweets_statistics = pd.concat([pd.read_csv("data/tweet_old.tsv", sep = "\t")[['id', 'like_count', 'retweet_count', 'reply_count', 'quote_count']].rename(columns = {"id":"tweet_id"}),
                              pd.read_csv("data/tweets-1679742620302.csv")])

## cols: user_id, handle, user_name; colnames do not match betweend old an new data. Even username and handle seem to be mixed up in new data set (inverse order)
## Info: Only a small amount of user_ids appear in both data sets, but if so username occasionaly have changed an therefore can not easily be merged
tweets_user = pd.read_csv("data/user_old.tsv", 
                          sep = "\t").rename(columns = {"id":"user_id","name": "user_name"} # uniform names
                                            ).merge(pd.read_csv("data/tweets-1679742702794.csv" # merge with renamed new data
                                                               ).rename(columns = {"username":"handle", "handle": "user_name"}), # reverse col names
                                                   on = "user_id", # user_id as matching column
                                                   how = "outer", # keep all unique uer_ids
                                                   suffixes = ["_2021", "_2022"]) # identify column where username and label came from

## Some usernames corresponding to one user_id have changed overtime. For easier handling only the latest username and handle is kept.
tweets_user = tweets_user.assign(handle    = tweets_user.apply(lambda row: row['handle_2021'] if pd.isna(row['handle_2022']) else row['handle_2022'], axis=1),
                                 user_name = tweets_user.apply(lambda row: row['user_name_2021'] if pd.isna(row['user_name_2022']) else row['user_name_2022'], axis=1)
                                ).drop(['handle_2021', 'handle_2022', 'user_name_2021', 'user_name_2022'], axis =1) # no longer needed

## addiditional information concerning the police stations
## cols: handle, name, typ, bundesland, stadt, lat, long
police_stations = pd.read_csv("data/polizei_accounts_geo.csv", sep = "\t"  
                             ).rename(columns = {"Polizei Account": "handle"})

tweets_meta.shape, tweets_statistics.shape, tweets_text.shape, tweets_user.shape, police_stations.shape

((479991, 3), (151690, 8), (151690, 4), (13327, 3), (163, 7))

Jetzt können noch alle Tweet bezogenen informationen in einem Data Frame gespeichert werden:

In [24]:
# Merge statistics, tweet text and user information in one data frame
tweets_combined = pd.merge(tweets_statistics, 
                           tweets_text,
                           on = 'tweet_id').merge(tweets_user, on = 'user_id'
                                                 ).drop(['id'], axis = 1) # drop unascessary id column (redundant to index)
 

In [49]:
# Convert datatypes to appropriate one
tweets_combined[['like_count', 'retweet_count', 'reply_count', 'quote_count']] = tweets_combined[['like_count', 'retweet_count', 'reply_count', 'quote_count']].fillna(np.NAN).astype(int)
tweets_combined = tweets_combined.assign(measured_at = pd.to_datetime(tweets_combined['measured_at']), # change date to date format
                                         created_at  = pd.to_datetime(tweets_combined['created_at']),
                                         handle      = tweets_combined['handle'].str.lower(), # handle to lower case
                                         is_deleted  = tweets_combined['is_deleted'].astype('boolean')) # is deleted column as boolean variable
tweets_combined#.to_csv("data/tweets_all_combined.csv")

tweet_id  like_count  retweet_count  reply_count  \
0       1321021123463663616           2              1            2   
1       1321037834246066181           2              0            0   
2       1321068234955776000          19              3            3   
3       1321073940199100416           0              0            0   
4       1321088646506754049           2              0            0   
...                     ...         ...            ...          ...   
151685  1625828803804004354           5              1            1   
151686  1628004105623900167           2              0            0   
151687  1628004810183016448           6              0            0   
151688  1628352896352878593           2              0            0   
151689  1628709531998998529          10              1            0   

        quote_count         measured_at  is_deleted  \
0                 0                 NaT        <NA>   
1                 0                 NaT        <NA>   
2                 0                 NaT        <NA>   
3                 0                 NaT        <NA>   
4                 0                 NaT        <NA>   
...             ...                 ...         ...   
151685            0 2023-02-19 13:40:36       False   
151686            0 2023-02-25 13:14:49       False   
151687            0 2023-02-25 13:14:49       False   
151688            0 2023-02-26 13:15:05       False   
151689            0 2023-02-27 12:17:33       False   

                                                                                                 tweet_text  \
0       @mahanna196 Da die Stadt keine Ausnahme für Radfahrer aufgeführt hat, gilt diese (Stand jetzt) a...   
1                                                                                       @mahanna196 Ja. *sr   
2       #Aktuell Auf dem ehem. Bundeswehrkrankenhausgelände in #Rostrup wurde ein Sprengsatz gefunden. F...   
3                                                       @Emma36166433 Bitte lesen Sie unseren Tweet 2/2 *sr   
4       In der vergangenen Woche wurde die Wohnung des Tatverdächtigen durchsucht. Dabei stellten die Be...   
...                                                                                                     ...   
151685  #Sicherheit durch #Sichtbarkeit\nUnsere #Dir3 hat zu diesem Thema wieder einmal die Puppen tanze...   
151686  Unser Präventionsteam vom #A44 berät heute und morgen tagsüber zum Thema Alkohol &amp; Drogen + ...   
151687  Auch unser #A52 war heute aktiv und hat zum Thema Alkohol &amp; Drogen im Straßenverkehr beraten...   
151688  Gestern führte unser #A13 in einer Wohnsiedlung einen Präventionseinsatz zum Thema „Wohnraumeinb...   
151689  Auf dem Gelände der @BUFAStudios (Oberlandstr. 26-35) findet heute die #Seniorenmesse vom Bezirk...   

                created_at              user_id           handle  \
0      2020-10-27 09:29:13   778895426007203840       polizei_ol   
1      2020-10-27 10:35:38   778895426007203840       polizei_ol   
2      2020-10-27 12:36:26   778895426007203840       polizei_ol   
3      2020-10-27 12:59:06   778895426007203840       polizei_ol   
4      2020-10-27 13:57:32   778895426007203840       polizei_ol   
...                    ...                  ...              ...   
151685 2023-02-15 12:06:07  1168873095614160896  polizeiberlin_p   
151686 2023-02-21 12:10:00  1168873095614160896  polizeiberlin_p   
151687 2023-02-21 12:12:48  1168873095614160896  polizeiberlin_p   
151688 2023-02-22 11:15:58  1168873095614160896  polizeiberlin_p   
151689 2023-02-23 10:53:07  1168873095614160896  polizeiberlin_p   

                                user_name  
0       Polizei Oldenburg-Stadt/Ammerland  
1       Polizei Oldenburg-Stadt/Ammerland  
2       Polizei Oldenburg-Stadt/Ammerland  
3       Polizei Oldenburg-Stadt/Ammerland  
4       Polizei Oldenburg-Stadt/Ammerland  
...                                   ...  
151685          Polizei Berlin Prävention  
151

### Adjazenzmatrix mentions
 
Information, welche nicht direkt enthalten ist: welche Accounts werden erwähnt. Ist nur im Tweet mit @handle gekennzeichnet.

In [53]:
# TODO

0    Auch wir schließen uns dem Apell an! \n\n#Ukra...
1    @BWeltenbummler Sehr schwer zu sagen. Die Evak...
2    Halten Sie durch – die Evakuierung ist fast ab...
3    Halten Sie durch – die Evakuierung ist fast ab...
4    RT @drkberlin_iuk: 🚨 In enger Abstimmung mit d...
Name: tweet_text, dtype: object

## Metadaten 

Welche Daten bilden die Grundlage?


In [112]:
tweets_meta["entity_type"].value_counts()
# tweets_meta[tweets_meta['entity_type'] == "mention"]

hashtag    267255
url        141594
mention     71142
Name: entity_type, dtype: int64

Insgesamt haben wir 151690 einzigartige Tweets:

In [113]:
tweets_combined["tweet_id"].value_counts().shape[0] # Anzahl an Tweets

151690

In [10]:
print("Die Tweets wurden vom", tweets_combined['created_at'].min().date(), "bis zum:", tweets_combined['created_at'].max().date(), "gesammelt.", "Also genau insgesamt:", (tweets_combined['created_at'].max() - tweets_combined['created_at'].min()).days, "Tage. (Mit kleinen Unterbrechungen)")
# tweets_combined[tweets_combined['created_at'] == tweets_combined['created_at'].max()] # Tweets vom letzten Tag

Die Tweets wurden vom 2020-10-27 bis zum: 2023-03-16 gesammelt. Also genau insgesamt: 870 Tage. (Mit kleinen Unterbrechungen)


Welche Polizei Accounts haben am meisten getweetet?

In [11]:
tweets_agg = tweets_combined.groupby(by = ["user_id", "user_name", "handle"]
                                    )["user_id"].aggregate(['count']
                                                          ).merge(police_stations,
                                                                  on = "handle",
                                                                  how = "left"
                                                                 ).sort_values(['count'], ascending=False)
tweets_agg.shape
activy_police_vis = tweets_agg[0:50]
activy_police_vis.head()

handle  count             Name      Typ           Bundesland  \
11     polizei_ffm   5512              NaN      NaN                  NaN   
0   polizeisachsen   5340  Polizei Sachsen  Polizei              Sachsen   
3   polizei_nrw_do   4895   Polizei NRW DO  Polizei  Nordrhein-Westfalen   
92       polizeibb   4323              NaN      NaN                  NaN   
61  polizeihamburg   4042  Polizei Hamburg  Polizei              Hamburg   

       Stadt         LAT        LONG  
11       NaN         NaN         NaN  
0    Dresden  51.0493286  13.7381437  
3   Dortmund  51.5142273   7.4652789  
92       NaN         NaN         NaN  
61   Hamburg   53.550341   10.000654

Visualisierung aktivste Polizeistadtionen:

In [13]:
barchart = alt.Chart(activy_police_vis[0:15]).mark_bar().encode(
    x = 'count:Q',
    y = alt.Y('handle:O', sort = '-x'),
)
barchart 

alt.Chart(...)

Welche Tweets ziehen besonders viel Aufmerksamkeit auf sich?

In [14]:
tweets_attention = tweets_combined.merge(police_stations,
                                         on = "handle",
                                         how = "left")
pd.options.display.max_colwidth = 100
tweets_attention.sort_values('like_count', ascending = False).reset_index()



index             tweet_id  like_count  retweet_count  reply_count  \
0         3053  1609539240458878979       21455           1845         3643   
1         1331  1355179228396879872       19186           3386         1203   
2        91693  1505620459148173316       15708           7098          186   
3        91695  1505620666476896259       10337           1539           59   
4       122631  1359098196434292739        9471            642          128   
...        ...                  ...         ...            ...          ...   
151685    7569  1332625325654757377         -99            -99          -99   
151686    7572  1332738525507186692         -99            -99          -99   
151687  144702  1465679768494526467         -99            -99          -99   
151688  144701  1464124290605977600         -99            -99          -99   
151689   66854  1376453040283209728         -99            -99          -99   

        quote_count         measured_at is_deleted  \
0               341 2023-01-05 14:44:34      False   
1               628                 NaT        NaN   
2               540 2022-03-24 20:15:08      False   
3                35 2022-03-24 20:15:08      False   
4               102                 NaT        NaN   
...             ...                 ...        ...   
151685          -99                 NaT        NaN   
151686          -99                 NaT        NaN   
151687          -99                 NaT        NaN   
151688          -99                 NaT        NaN   
151689          -99                 NaT        NaN   

                                                                                                 tweet_text  \
0       Die Gewalt, die unsere Kolleginnen &amp; Kollegen in der Silvesternacht erleben mussten, ist une...   
1       An diejenigen, die vergangene Nacht in eine Schule in #Gesundbrunnen eingebrochen sind und 242 T...   
2       WICHTIGE Info:\nÜber das Internet wird derzeit ein Video verbreitet, in dem von einem Überfall a...   
3       Die Experten gehen derzeit davon aus, dass es sich um ein absichtliches "Fake-Video" handelt, da...   
4                                           Weil wir dich schieben! @BVG_Kampagne 😉 https://t.co/N8kdlCxhz2   
...                                                                                                     ...   
151685  Sinken die Temperaturen ❄, steigt zeitgleich das Risiko für Verkehrsteilnehmer. Höchste Zeit zu ...   
151686  📺Am Sonntag, um 19:50 Uhr, geht es bei #KripoLive im \n@mdrde\n auch um die Fahndung nach einem ...   
151687  Musik verbindet!\nUnser #Adventskalender der #Bundespolizei startet morgen ➡ https://t.co/V6CaTV...   
151688  @gretchen_hann Hallo, diese Frage kann die Bundespolizei Spezialkräfte besser beantworten. Richt...   
151689  #Bönen #Holzwickede - Verstöße gegen Coronaschutzverordnung: Polizei löst Gaststättenabend und F...   

                created_at     user_id          handle             user_name  \
0      2023-01-01 13:17:13  2397974054   polizeiberlin        Polizei Berlin   
1      2021-01-29 15:41:20  2397974054   polizeiberlin        Polizei Berlin   
2      2022-03-20 19:01:05  2389161066  polizei_nrw_bn        Polizei NRW BN   
3      2022-03-20 19:01:54  2389161066  polizei_nrw_bn        Polizei NRW BN   
4      2021-02-09 11:13:55  4876039738          bpol_b  Bundespolizei Berlin   
...                    ...         ...             ...                   ...   
151685 2020-11-28 10:00:11   223758384  polizeisachsen       Polizei Sachsen   
151686 2020-11-28 17:30:00   223758384  polizeisachsen       Polizei Sachsen   
151687 2021-11-30 13:51:02  4876085224       bpol_nord    Bundespolizei Nord   
151688 2021-11-26 06:50:07  4876085224       bpol_nord    Bundespolizei Nord   
151689 2021-03-29 08:35:52  2389263558  polizei_nrw_un        Polizei NRW UN   

                   Name      Typ           Bundesland    Stadt         LAT  \
0                   NaN      NaN       

user_id          handle         user_name
0      1000004686156652545        6jannik9  Systemstratege: 
1      1000043230870867969         LSollik        Physiolucy
2      1000405847460151296   Achim1949Hans  Systemstratege: 
3      1000460805719121921          WahreW        WahreWorte
4      1000744009638252544        derD1ck3        Ⓓ①ⓒⓚ①③ (🏡)
...                    ...             ...               ...
11554             99931264       Havok1975  Systemstratege: 
11555   999542638226403328  Madame_de_Saxe  Systemstratege: 
11556   999901133282754560   tungstendie74  Systemstratege: 
11557   999904275080794112     _danielheim  Systemstratege: 
11558   999955376454930432      amyman6010  Systemstratege: 

[11559 rows x 3 columns]